In [1]:
from collections import Counter, defaultdict

In [2]:
lis = [1, 2, 3, 4, 5, 6, 7]
tuple(lis[:len(lis)-1])

(1, 2, 3, 4, 5, 6)

## A basic n-gram generator

In [3]:
def reg_tokenize(sent):
    return re.findall(r'[A-Z0-9a-z]+[A-Z0-9a-z._%+-]*@[A-Z0-9a-z]+(?:\.[A-Z0-9a-z]+)+|(?<= )[$€£¥₹]?[0-9]+(?:[,.][0-9]+)*[$€£¥₹]?|(?:(?:https?:\/\/(?:www.)?)|www.)[A-Z0-9a-z_-]+(?:\.[A-Z0-9a-z_\/-]+)+|(?<= )@[A-Z0-9a-z._%+]+|#[A-Za-z0-9]+(?:\.[A-Za-z0-9]+)*|\.{3,}|[!"#$%&\'()*+,\-./:;<=>?@\[\\\]\^_`{\|}~]|\w+', sent)

def new_reg_tokenize(sent):
    fin = re.findall(r'[\U00010000-\U0010ffff]'\
                     r'|[A-Z0-9a-z]+[A-Z0-9a-z._%+-]*@[A-Z0-9a-z]+(?:\.[A-Z0-9a-z]+)+'\
                     r'|(?<= )[$€£¥₹]?[0-9]+(?:[,.][0-9]+)*[$€£¥₹]?'\
                     r'|(?:(?:https?:\/\/(?:www.)?)|www.)[A-Z0-9a-z_-]+(?:\.[A-Z0-9a-z_\/-]+)+'\
                     r'|(?:(?<=[^A-Za-z0-9])|^)@[A-Z0-9a-z._+]+[A-Za-z0-9_]'\
                     r'|#[A-Za-z0-9]+(?:[\._-][A-Za-z0-9]+)*'\
                     r'|\.{3,}'\
                     r'|[!"#$%\&\'()*+,\-.:;<=>?@\[\\\/\]\^_`{\|}~]'\
                     r'|[A-Z]\.'\
                     r'|\w+', sent)
    return fin

In [4]:
import re
# from nltk.tokenize import word_tokenize

def ngrams(sentence, n):
    '''
    This currently does not accomodate for numbers with punctuation.
    '''
#     sentence = sentence.lower()
    
    tokens = new_reg_tokenize(sentence)
    
    ngrams = zip(*[tokens[i:] for i in range(n)])
    return [ngram for ngram in ngrams]

In [5]:
t = '''Nice car, bro.
Thanks let's get going.'''
ngrams(t, n=3)

[('Nice', 'car', ','),
 ('car', ',', 'bro'),
 (',', 'bro', '.'),
 ('bro', '.', 'Thanks'),
 ('.', 'Thanks', 'let'),
 ('Thanks', 'let', "'"),
 ('let', "'", 's'),
 ("'", 's', 'get'),
 ('s', 'get', 'going'),
 ('get', 'going', '.')]

In [22]:
def create_model(file="../corpus3.txt", n=3):
    '''
    Takes a file to train on, an 'n'
    Returns predictive n-gram model
    '''
    
    # Create a placeholder for model
    model = defaultdict(lambda: defaultdict(lambda: 0))
    incv = defaultdict(lambda: defaultdict(lambda: 0))

    with open(file, 'r') as f:
#         for piece in read_in_chunks(f, chunk_size=2097152):
        
        for line in f:
            for i in range(1, n+1):
                for ngram in ngrams(line, n=i):
                    wprec = tuple(ngram[:i-1])
                    waft = ngram[i-1]
                    model[wprec][waft] += 1
                    if i >= 2:
                        incv[waft][wprec] += 1
        f.close()    

#     for wprec in model:
#         total_count = float(sum(model[wprec].values()))
#         for waft in model[wprec]:
#             model[wprec][waft] /= total_count
            
    return model, incv

In [23]:
%%time
model, incv = create_model(n=3)

CPU times: user 598 ms, sys: 17.4 ms, total: 615 ms
Wall time: 617 ms


In [24]:
model

defaultdict(<function __main__.create_model.<locals>.<lambda>()>,
            {(): defaultdict(<function __main__.create_model.<locals>.<lambda>.<locals>.<lambda>()>,
                         {'This': 147,
                          'is': 1551,
                          'the': 2825,
                          'shop': 18,
                          'where': 71,
                          'I': 1768,
                          'bought': 67,
                          'my': 268,
                          'bike': 5,
                          '.': 7738,
                          'The': 857,
                          'driver': 4,
                          'drinks': 6,
                          'liquor': 3,
                          ',': 1172,
                          'think': 91,
                          'someone': 5,
                          'else': 22,
                          'ought': 6,
                          'to': 1813,
                          'drive': 7,
                          'wo

In [25]:
incv

defaultdict(<function __main__.create_model.<locals>.<lambda>()>,
            {'is': defaultdict(<function __main__.create_model.<locals>.<lambda>.<locals>.<lambda>()>,
                         {('This',): 62,
                          ('He',): 163,
                          ('Amit',): 1,
                          ('clock',): 1,
                          ('alarm', 'clock'): 1,
                          ('Ram',): 8,
                          ('Kanwar', 'Ram'): 1,
                          ('It',): 112,
                          ('she',): 16,
                          ('days', 'she'): 1,
                          ('house',): 13,
                          ('His', 'house'): 3,
                          ('Deepak',): 1,
                          ('here',): 4,
                          ('said', 'here'): 1,
                          ('Thames',): 1,
                          ('River', 'Thames'): 1,
                          ('life',): 1,
                          ('Her', 'life'): 1,
           

In [7]:
for seq in model:
    total_count = float(sum(model[seq].values()))
    for predicted in model[seq]:
        print('For {0} predicted {1} with P={2}'.format(seq, predicted, model[seq][predicted]/total_count))

For () predicted This with P=0.0017870385003464666
For () predicted is with P=0.018855079687329045
For () predicted the with P=0.03434274669033176
For () predicted shop with P=0.00021882104085875102
For () predicted where with P=0.0008631274389428512
For () predicted I with P=0.02149308890212621
For () predicted bought with P=0.0008145005409742399
For () predicted my with P=0.0032580021638969597
For () predicted bike with P=6.078362246076417e-05
For () predicted . with P=0.09406873412027864
For () predicted The with P=0.010418312889774978
For () predicted driver with P=4.862689796861134e-05
For () predicted drinks with P=7.2940346952917e-05
For () predicted liquor with P=3.64701734764585e-05
For () predicted , with P=0.014247681104803123
For () predicted think with P=0.0011062619287859079
For () predicted someone with P=6.078362246076417e-05
For () predicted else with P=0.00026744793882736234
For () predicted ought with P=7.2940346952917e-05
For () predicted to with P=0.022040141504273

For () predicted cargo with P=1.2156724492152835e-05
For () predicted Hary with P=1.2156724492152835e-05
For () predicted each with P=0.00024313448984305668
For () predicted Jane with P=0.00015803741839798683
For () predicted Letters with P=1.2156724492152835e-05
For () predicted quiz with P=2.431344898430567e-05
For () predicted modem with P=1.2156724492152835e-05
For () predicted classical with P=1.2156724492152835e-05
For () predicted music with P=0.000145880693905834
For () predicted peak with P=1.2156724492152835e-05
For () predicted allow with P=3.64701734764585e-05
For () predicted smoke with P=6.078362246076417e-05
For () predicted desire with P=7.2940346952917e-05
For () predicted wealth with P=7.2940346952917e-05
For () predicted acquire with P=3.64701734764585e-05
For () predicted quick with P=2.431344898430567e-05
For () predicted between with P=0.00010941052042937551
For () predicted crucial with P=2.431344898430567e-05
For () predicted pulses with P=3.64701734764585e-05
F

For () predicted behaved with P=3.64701734764585e-05
For () predicted precautions with P=1.2156724492152835e-05
For () predicted climbers with P=1.2156724492152835e-05
For () predicted Feeling with P=1.2156724492152835e-05
For () predicted sorts with P=1.2156724492152835e-05
For () predicted haughtily with P=1.2156724492152835e-05
For () predicted pillars with P=1.2156724492152835e-05
For () predicted Barrage with P=1.2156724492152835e-05
For () predicted Young with P=2.431344898430567e-05
For () predicted computers with P=3.64701734764585e-05
For () predicted relinquished with P=1.2156724492152835e-05
For () predicted democracy with P=1.2156724492152835e-05
For () predicted Kalidas with P=1.2156724492152835e-05
For () predicted manager with P=4.862689796861134e-05
For () predicted salary with P=2.431344898430567e-05
For () predicted managing with P=3.64701734764585e-05
For () predicted image with P=1.2156724492152835e-05
For () predicted Honest with P=1.2156724492152835e-05
For () pre

For () predicted giggled with P=1.2156724492152835e-05
For () predicted paying with P=1.2156724492152835e-05
For () predicted craft with P=1.2156724492152835e-05
For () predicted Headmaster with P=1.2156724492152835e-05
For ('This',) predicted is with P=0.4217687074829932
For ('This',) predicted continued with P=0.006802721088435374
For ('This',) predicted done with P=0.006802721088435374
For ('This',) predicted poor with P=0.006802721088435374
For ('This',) predicted will with P=0.027210884353741496
For ('This',) predicted gave with P=0.006802721088435374
For ('This',) predicted gutter with P=0.006802721088435374
For ('This',) predicted institution with P=0.013605442176870748
For ('This',) predicted must with P=0.006802721088435374
For ('This',) predicted man with P=0.02040816326530612
For ('This',) predicted civilization with P=0.006802721088435374
For ('This',) predicted basket with P=0.006802721088435374
For ('This',) predicted bunglow with P=0.006802721088435374
For ('This',) pred

For ('The',) predicted value with P=0.0011668611435239206
For ('The',) predicted doctors with P=0.002333722287047841
For ('The',) predicted Lover with P=0.0011668611435239206
For ('The',) predicted sun with P=0.005834305717619603
For ('The',) predicted program with P=0.0011668611435239206
For ('The',) predicted court with P=0.0011668611435239206
For ('The',) predicted committee with P=0.002333722287047841
For ('The',) predicted cost with P=0.0011668611435239206
For ('The',) predicted crow with P=0.003500583430571762
For ('The',) predicted old with P=0.008168028004667444
For ('The',) predicted Lord with P=0.0011668611435239206
For ('The',) predicted cautious with P=0.0011668611435239206
For ('The',) predicted proverb with P=0.0011668611435239206
For ('The',) predicted minstrel with P=0.002333722287047841
For ('The',) predicted strike with P=0.0011668611435239206
For ('The',) predicted telegraph with P=0.0011668611435239206
For ('The',) predicted letters with P=0.002333722287047841
For (

...

For ('top',) predicted shelf with P=0.125
For ('top',) predicted boarding with P=0.125
For ('top',) predicted of with P=0.375
For ('top',) predicted , with P=0.125
For ('speed',) predicted . with P=1.0
For ('He', 'ran') predicted at with P=0.07692307692307693
For ('He', 'ran') predicted away with P=0.38461538461538464
For ('He', 'ran') predicted to with P=0.15384615384615385
For ('He', 'ran') predicted as with P=0.07692307692307693
For ('He', 'ran') predicted . with P=0.07692307692307693
For ('He', 'ran') predicted a with P=0.15384615384615385
For ('He', 'ran') predicted so with P=0.07692307692307693
For ('ran', 'at') predicted top with P=1.0
For ('at', 'top') predicted speed with P=1.0
For ('top', 'speed') predicted . with P=1.0
For ('landed',) predicted at with P=0.3333333333333333
For ('landed',) predicted spread with P=0.3333333333333333
For ('landed',) predicted there with P=0.3333333333333333
For ('Karanchi',) predicted , with P=0.5
For ('Karanchi',) predicted . with P=0.5
For ('

For ('whether', 'he') predicted lives with P=0.2
For ('whether', 'he') predicted is with P=0.2
For ('whether', 'he') predicted might with P=0.2
For ('Fiona',) predicted is with P=0.2
For ('Fiona',) predicted visited with P=0.2
For ('Fiona',) predicted visiting with P=0.2
For ('Fiona',) predicted has with P=0.2
For ('Fiona',) predicted had with P=0.2
For ('grandma',) predicted . with P=0.6666666666666666
For ('grandma',) predicted ? with P=0.16666666666666666
For ('grandma',) predicted bought with P=0.16666666666666666
For ('Fiona', 'is') predicted not with P=1.0
For ('visit', 'her') predicted grandma with P=1.0
For ('her', 'grandma') predicted . with P=0.8
For ('her', 'grandma') predicted ? with P=0.2
For ('tenth',) predicted or with P=1.0
For ('twelfth',) predicted letter with P=1.0
For ('Is', 'it') predicted the with P=0.1111111111111111
For ('Is', 'it') predicted a with P=0.1111111111111111
For ('Is', 'it') predicted an with P=0.1111111111111111
For ('Is', 'it') predicted Ram with P

For ('sore', 'about') predicted the with P=1.0
For ('the', 'insulting') predicted behaviour with P=1.0
For ('insulting', 'behaviour') predicted meted with P=1.0
For ('behaviour', 'meted') predicted out with P=1.0
For ('meted', 'out') predicted by with P=1.0
For ('out', 'by') predicted Moomal with P=0.5
For ('out', 'by') predicted the with P=0.5
For ('by', 'Moomal') predicted . with P=1.0
For ('Ram', 'arrived') predicted home with P=1.0
For ('arrived', 'home') predicted late with P=0.5
For ('arrived', 'home') predicted at with P=0.5
For ('late', 'yesterday') predicted . with P=1.0
For ('Rama', 'asked') predicted me with P=1.0
For ('asked', 'me') predicted what with P=0.3333333333333333
For ('asked', 'me') predicted if with P=0.1111111111111111
For ('asked', 'me') predicted whether with P=0.2222222222222222
For ('asked', 'me') predicted when with P=0.1111111111111111
For ('asked', 'me') predicted to with P=0.1111111111111111
For ('asked', 'me') predicted . with P=0.1111111111111111
For (

For ('talk', 'to') predicted your with P=0.14285714285714285
For ('talk', 'to') predicted him with P=0.14285714285714285
For ('you', 'because') predicted you with P=1.0
For ('you', 'were') predicted far with P=0.1
For ('you', 'were') predicted here with P=0.2
For ('you', 'were') predicted coming with P=0.1
For ('you', 'were') predicted asking with P=0.1
For ('you', 'were') predicted absent with P=0.1
For ('you', 'were') predicted going with P=0.2
For ('you', 'were') predicted saying with P=0.1
For ('you', 'were') predicted on with P=0.1
For ('were', 'far') predicted away with P=1.0
For ('far', 'away') predicted . with P=1.0
For ('laughing',) predicted so with P=0.13333333333333333
For ('laughing',) predicted . with P=0.4
For ('laughing',) predicted about with P=0.06666666666666667
For ('laughing',) predicted at with P=0.06666666666666667
For ('laughing',) predicted man with P=0.06666666666666667
For ('laughing',) predicted loudly with P=0.06666666666666667
For ('laughing',) predicted o

KeyboardInterrupt: 

In [ ]:
def perplexity(file='../corpus3.txt', model, n):
    
    perlexity = 1
    
    
            
#     test = ngrams(t)
#     perplexity = 1
#     N = 0
#     for word in testset:
#         N += 1
#         perplexity = perplexity * (1/model[word])
#     perplexity = pow(perplexity, 1/float(N)) 
    return perplexity